# Characteristics IQ

- Variance Fractal Dimension Trajectory over magnitude and phase(Per τ and T)
    - Average of magnitude vdtf     (Overall)
    - Variance of magnitude vdtf    (Overall)
    - Average of Phase vdtf         (Overall)
    - Variance of Phase vdtf        (Overall) 
- Phase Noise (Per τ and T) (Jitter)
    - Variance (Overall)
- sample variance of the fractional frequency fluctuations (FC and FS) (Per τ and T)
    - Allan Deviation: how much the oscillators wander in the time scale (Overall)
    - Flicker Noise ??? 
- IQ Imbalance (Per τ and T)
    - IQ Imbalance (Overall)
- Phasor Noise Deviation (Per τ and T)  (PA Non Linearities)
    - Variance (Overall)


## Import Libraries

In [1]:
import numpy as np
from analysis_functions_v2 import *
import allantools


2025-05-12 10:54:10.585392: I external/local_xla/xla/tsl/cuda/cudart_stub.cc:32] Could not find cuda drivers on your machine, GPU will not be used.
2025-05-12 10:54:10.590578: I external/local_xla/xla/tsl/cuda/cudart_stub.cc:32] Could not find cuda drivers on your machine, GPU will not be used.
2025-05-12 10:54:10.606293: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:485] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2025-05-12 10:54:10.634077: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:8454] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2025-05-12 10:54:10.641895: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1452] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-05-12 10:54:11.934479: W tensorflow/compiler/tf2tensorrt/utils/p

# Import Signal

In [2]:
features_dir = "../../features_v2/" # Define the relative directory path for the features folder
os.makedirs(features_dir, exist_ok=True) # Ensure the features directory exists, create it if it doesn't

data_dir = "../../data/"

sufix = 2
sample = 15  #0 - 9999
fs = 25e6  #sample_frequency
dt = 1/25e6 #period

samples, fcs = load_samples(data_dir,f"{sufix:03d}")
ra_sat, ra_cell = load_data(data_dir, f"{sufix:03d}")

fc = fcs[sample]

# Obtain I[0] and Q[1] signals
i_signal = samples[sample,:,0]
q_signal = samples[sample,:,1]


print('Done')

Done


### Variance Fractal Dimension Trajectory (Per τ and T)

In [5]:
def vfdt(window_mag: np.ndarray,
            window_phase: np.ndarray,
            win_length: int):
    """
    Compute VFDT values for a single window of magnitude and unwrapped phase.

    Parameters:
      window_mag (np.ndarray): magnitude samples for this window, length L
      window_phase (np.ndarray): unwrapped phase samples for this window, length L
      win_length (int): window length L

    Returns:
      vfdt_magnitude (float)
      vfdt_phase     (float)
    """
    # magnitude differences
    diff_mag = window_mag[1:] - window_mag[:-1]
    var_mag  = np.var(diff_mag)
    if var_mag <= 0:
        vfdt_magnitude = 2.0
    else:
        vfdt_magnitude = 2 - (np.log(var_mag) / (2 * np.log(win_length)))

    # phase differences
    diff_phase = window_phase[1:] - window_phase[:-1]
    var_phase  = np.var(diff_phase)
    if var_phase <= 0:
        vfdt_phase = 2.0
    else:
        vfdt_phase = 2 - (np.log(var_phase) / (2 * np.log(win_length)))

    return vfdt_magnitude, vfdt_phase

### Phase Noise

In [13]:
def phase_noise(window_i: np.ndarray,
                window_q: np.ndarray,
                fs: float,
                remove_amplitude_variation: bool = True,
                polynomial_degree: int = 1) -> float:
    """
    Compute the variance of detrended, unwrapped phase (“phase noise”) from I/Q samples.

    Parameters
    ----------
    window_i : np.ndarray
        In-phase samples (1D).
    window_q : np.ndarray
        Quadrature samples (1D), same length as window_i.
    fs : float
        Sampling frequency in Hz (must be > 0).
    remove_amplitude_variation : bool
        If True, normalize out amplitude modulation before phase extraction.
    polynomial_degree : int
        Degree of polynomial to fit & remove (must be ≥ 0).

    Returns
    -------
    float
        Variance of the detrended, unwrapped phase.
    """
    # ——— Validation ———
    if window_i.ndim != 1 or window_q.ndim != 1:
        raise ValueError("window_i and window_q must be 1-D arrays")
    if window_i.shape != window_q.shape:
        raise ValueError("window_i and window_q must have the same length")
    if fs <= 0:
        raise ValueError("Sampling frequency fs must be positive")
    
    N = window_i.size
    # Cap polynomial_degree so polyfit doesn’t blow up
    if polynomial_degree < 0:
        raise ValueError("polynomial_degree must be non-negative")
    if polynomial_degree >= N:
        polynomial_degree = N - 1

    # ——— Build complex signal ———
    cplx = window_i + 1j * window_q

    # ——— 1) Remove amplitude variation ———
    if remove_amplitude_variation:
        mags = np.abs(cplx)
        cplx = cplx / (mags + 1e-12)

    # ——— 2) Instantaneous phase & unwrap ———
    phase = np.angle(cplx)
    phase_unwrapped = np.unwrap(phase)

    # ——— 3) Polynomial detrend of phase ———
    t = np.arange(N) / fs
    # fit & subtract
    p_fit = np.polyfit(t, phase_unwrapped, deg=polynomial_degree)
    phase_fit = np.polyval(p_fit, t)
    phase_detrended = phase_unwrapped - phase_fit

    ph_noise = np.var(phase_detrended)

    # ——— 4) Return variance ———
    return ph_noise

### sample variance of the fractional frequency fluctuations 

In [22]:
def sample_variance_and_allan(y: np.ndarray,
                              fs: float,
                              win_length: int,
                              win_shift: int) -> Tuple[float, np.ndarray, float]:
    """
    Compute time-domain sample variance and Allan deviation of fractional frequency fluctuations.

    Parameters
    ----------
    y : np.ndarray
        1D array of fractional frequency deviation samples.
    fs : float
        Sampling rate in Hz.
    win_length : int
        Window length (samples) for averaging (m).
    win_shift : int
        Shift (samples) between consecutive windows (M).

    Returns
    -------
    sigma2 : float
        Unbiased sample variance of block-averaged deviations.
    y_bar : np.ndarray
        Block-averaged fractional deviations (length N).
    sigma_y : float
        Allan deviation computed as sqrt(0.5 * mean(diff(y_bar)**2)).
    """
    # Input validation
    if win_length <= 0 or win_shift <= 0:
        raise ValueError("win_length and win_shift must be positive integers")
    if win_length > len(y):
        raise ValueError("win_length is larger than the length of y")
    
    # Compute averaging and repetition intervals
    tau = win_length / fs
    T   = win_shift / fs

    # Number of full, non-overlapping windows
    N = 1 + (len(y) - win_length) // win_shift
    if N < 1:
        raise ValueError("Not enough data points for even one window")
    
    # Compute block averages ȳ_k
    y_bar = np.array([
        y[k*win_shift : k*win_shift + win_length].mean()
        for k in range(N)
    ])
    
    # Sample variance (unbiased)
    sigma2 = np.var(y_bar, ddof=1) if N > 1 else 0.0

    # Allan deviation σ_y = sqrt(0.5 * mean((ȳ_{k+1}-ȳ_k)^2))
    if N > 1:
        diffs = np.diff(y_bar)
        sigma2_allan = 0.5 * np.mean(diffs**2)
        sigma_y = np.sqrt(sigma2_allan)
    else:
        sigma_y = 0.0

    return y_bar, sigma2, sigma_y

### IQ Imbalance

In [15]:
def estimate_iq_imbalance(window_i: np.ndarray,
                          window_q: np.ndarray) -> Tuple[float, float]:
    """
    Estimate I/Q gain and phase imbalance from windowed I and Q samples.

    Parameters
    ----------
    window_i : np.ndarray, shape (N,)
        In-phase (I) samples of the IQ signal window.
    window_q : np.ndarray, shape (N,)
        Quadrature (Q) samples of the IQ signal window.

    Returns
    -------
    epsilon_est : float
        Estimated relative gain error (ε), defined as (gain_Q / gain_I) - 1.
    phi_est : float
        Estimated phase error (φ) in radians between I and Q channels.

    Raises
    ------
    ValueError
        If the input arrays are not 1D and of equal length,
        or if the computed denominator for gain estimation is non-positive.
    """
    # Stack I and Q into an (N, 2) array for unified processing
    iq_signal = np.column_stack((window_i, window_q))

    # Validate input dimensions: must be 2D with two columns
    if iq_signal.ndim != 2 or iq_signal.shape[1] != 2:
        raise ValueError("window_i and window_q must be 1D arrays of equal length to form shape (N, 2).")

    # Remove DC offset by demeaning each channel
    I = iq_signal[:, 0] - np.mean(iq_signal[:, 0])
    Q = iq_signal[:, 1] - np.mean(iq_signal[:, 1])

    # Compute variances of each channel and their covariance
    var_I = np.var(I)          # Variance of the I channel
    var_Q = np.var(Q)          # Variance of the Q channel
    cov_IQ = np.mean(I * Q)    # Covariance between I and Q

    # Estimate phase error φ from cov(I, Q) / var(Q) = -tan(φ)
    phi_est = -np.arctan(cov_IQ / var_Q)

    # Compute denominator for gain estimation: var(I)*cos²(φ) - var(Q)*sin²(φ)
    denom = var_I * (np.cos(phi_est)**2) - var_Q * (np.sin(phi_est)**2)
    if denom <= 0:
        raise ValueError("Invalid covariance values: denominator for gain estimation is non-positive.")

    # Estimate squared gain factor: (1 + ε)² = var(Q) / denom
    gain_factor_squared = var_Q / denom

    # Derive ε: ε = sqrt((1 + ε)²) - 1
    epsilon_est = np.sqrt(gain_factor_squared) - 1

    return epsilon_est, phi_est

### Processor

In [ ]:
def IQ_feature_processor_V3(i_signal: np.ndarray,
                            q_signal: np.ndarray,
                            win_length: int,
                            win_shift: int,
                            fs: float,
                            fc:float,
                            pn_band: Tuple[float, float] = (1e3, 1e5)
                           ) -> dict:
    
    # Calculate the magnitude and phase of the IQ signal
    complex_signal = i_signal + 1j * q_signal
    mag = np.abs(complex_signal)
    phase = np.angle(complex_signal)

    # Unwrap phase to remove discontinuities at ±π
    phase_unwrapped = np.unwrap(phase)

    f_inst = np.diff(phase) * fs * ( 1 / (2 * np.pi))  # gamma*
    y = (f_inst - fc) / fc # fractional instantaneous frequency deviation (y)

    M = (len(mag) - win_length) // win_shift + 1
    features = {k: np.zeros(M) for k in [
        "v_vfdt_mag", 
        "v_vfdt_ph", 
        "v_noise_ph",
        "v_frac_freq_var",
        "v_iq_imb_phi_est",       # Estimate phase error φ
        "v_iq_imb_epsilon_est",   # Derive ε
        "v_win_idx"
    ]}

    idx = 0
    for start in range(0, len(mag) - win_length + 1, win_shift):
        end = start + win_length
        win_i = i_signal[start:end]
        win_q = q_signal[start:end]
        win_mag = mag[start:end]
        win_ph  = phase_unwrapped[start:end]

        # VFDT
        features["v_vfdt_mag"][idx], features["v_vfdt_ph"][idx] = vfdt(win_mag, win_ph, win_length)

        # PHASE NOISE
        features["v_noise_ph"][idx] = phase_noise(win_i, win_q, fs, remove_amplitude_variation = True, polynomial_degree = 1)

        # FRACTIONAL FREQUENCY FLUCTUATIONS
        # it is computed outside the for loop

        # IQ IMBALANCE
        v_epsilon_est, v_phi_est = estimate_iq_imbalance(win_i, win_q)
        features["v_iq_imb_epsilon_est"][idx] = v_epsilon_est
        features["v_iq_imb_phi_est"][idx] =  v_phi_est
        # WINDONW INDEX
        features["v_win_idx"][idx] = start

        idx += 1
    
    # FRACTIONAL FREQUENCY FLUCTUATIONS
    y_bar, sigma2, sigma_y = sample_variance_and_allan(y, fs, win_length, win_shift)
    features["v_frac_freq_var"] = y_bar


    # ----------- STATISTICS FOR THE WHOLE SIGNAL --------------------- 

    # VFDT 
    features["e_vfdt_avg_mag"]  = np.full(1, np.mean(features["v_vfdt_mag"])) #Average of magnitude vdtf
    features["e_vfdt_var_mag"]  = np.full(1, np.var(features["v_vfdt_mag"]))  #Variance of magnitude vdtf
    features["e_vfdt_avg_ph"]   = np.full(1, np.mean(features["v_vfdt_ph"])) #Average of Phase vdtf
    features["e_vfdt_var_ph"]   = np.full(1, np.var(features["v_vfdt_ph"]))  #Variance of Phase vdtf

    #PHASE NOISE
    features["e_noise_ph_var"]  = np.full(1, np.var(features["v_noise_ph"]))

    # FRACTIONAL FREQUENCY FLUCTUATIONS
    features["e_frac_freq_sigma2"]     = np.full(1, sigma2) # Sigma 2 of y_bar
    features["e_frac_freq_allan_dev"]  = np.full(1, sigma_y) # Allan deviation of y_bar  

    #IQ IMBALANCE

    
    # epsilon_est, phi_est = estimate_iq_imbalance(i_signal, q_signal)

    # features["e_iq_imb_epsilon_est"] = np.full(1,epsilon_est)
    # features["e_iq_imb_phi_est"] = np.full(1,phi_est)

    return features



#### Metadata

In [5]:
def create_metadata_from_features_dict(features_dict: dict,
                                       sat_label: int,
                                       transmitter_label: int,
                                       feature_counter: int,
                                       fs: float,
                                       win_length: int,
                                       win_shift: int,
                                       fc: float
                                      ) -> dict:
    """
    Generate metadata for a pre-computed features dictionary without altering it.

    Args:
      features_dict: dict mapping feature_name -> 1D array of values
      sat_label: Integer label for the satellite
      transmitter_label: Integer label for the transmitter
      feature_counter: Integer used to name this feature set (e.g. 2 → "features_2")
      fs: Sampling frequency in Hz
      win_length: Window length in samples
      win_shift: Window shift in samples
      fc: Center frequency in Hz

    Returns:
      metadata: dict containing only JSON-serializable types:
        - Satellite_Label (int)
        - Transmitter_Label (int)
        - Feature_Dictionary_Name (str)
        - Sampling_Frequency (float)
        - Win_Length (int)
        - Win_Shift (int)
        - Center_Frequency (float)
        - Rows (list of str)
        - Row_Lengths (list of int)
    """
    # Cast numeric inputs to built-in types to ensure JSON serializability
    sat_label = int(sat_label)
    transmitter_label = int(transmitter_label)
    fs = float(fs)
    win_length = int(win_length)
    win_shift = int(win_shift)
    fc = float(fc)

    feature_dictionary_name = f"features_{int(feature_counter)}"
    rows = list(map(str, features_dict.keys()))
    # Ensure row lengths are Python ints
    row_lengths = [int(len(features_dict[row])) for row in rows]

    metadata = {
        "Satellite_Label":        sat_label,
        "Transmitter_Label":      transmitter_label,
        "Feature_Dictionary_Name": feature_dictionary_name,
        "Sample_Frequency":        fs,
        "Win_Length":             win_length,
        "Win_Shift":              win_shift,
        "Center_Frequency":       fc,
        "Rows":                   rows,
        "Row_Lengths":            row_lengths
    }
    return metadata

#### Run Features and Metadata

In [3]:
win_length = 50
win_shift = 50

features = IQ_feature_processor_V3(i_signal, q_signal, win_length, win_shift, fs, fc)
metadata = create_metadata_from_features_dict(
    features_dict     = features,
    sat_label         = 63,
    transmitter_label = 7,
    feature_counter   = 2,
    fs                = fs,
    win_length        = win_length,
    win_shift         = win_shift,
    fc                = fc
)

print(metadata)

{'Satellite_Label': 63, 'Transmitter_Label': 7, 'Feature_Dictionary_Name': 'features_2', 'Sample_Frequency': 25000000.0, 'Win_Length': 50, 'Win_Shift': 50, 'Center_Frequency': 1626303232.0, 'Rows': ['v_vfdt_mag', 'v_vfdt_ph', 'v_noise_ph', 'v_frac_freq_var', 'v_iq_imb_phi_est', 'v_iq_imb_epsilon_est', 'v_win_idx', 'e_vfdt_avg_mag', 'e_vfdt_var_mag', 'e_vfdt_avg_ph', 'e_vfdt_var_ph', 'e_noise_ph_var', 'e_frac_freq_sigma2', 'e_frac_freq_allan_dev', 'e_iq_imb_epsilon_est', 'e_iq_imb_phi_est'], 'Row_Lengths': [220, 220, 220, 219, 220, 220, 220, 1, 1, 1, 1, 1, 1, 1, 1, 1]}


#### Save data

In [82]:
# Save the feature matrix and metadata to the features folder
np.save(os.path.join(features_dir, f"{metadata['Feature_Dictionary_Name']}.npy"), features)
with open(os.path.join(features_dir, f"{metadata['Feature_Dictionary_Name']}_metadata.json"), "w") as f:
    json.dump(metadata, f, indent=2)

In [12]:
def get_signals_v2(df: pd.DataFrame, sat_id=None, cell_id=None):
    """
    Returns the signals and center‐frequency values associated with a satellite (sat_id),
    a cell (cell_id), or both.

    Args:
        df (pd.DataFrame): DataFrame indexed or with columns 'ra_sat', 'ra_cell',
                           containing columns 'fcs' and 'samples'.
        sat_id (int, optional): Satellite ID to filter by.
        cell_id (int, optional): Cell ID to filter by.

    Returns:
        - If both sat_id and cell_id: list of (fc, samples) tuples.
        - If only sat_id:           list of (cell_id, fc, samples) tuples.
        - If only cell_id:          list of (sat_id, fc, samples) tuples.
        - None if no criteria given or no matches found.
    """
    # No filter means nothing to return
    if sat_id is None and cell_id is None:
        return None

    # Make sure 'ra_sat', 'ra_cell', 'fcs' are columns for easy filtering
    if {'ra_sat', 'ra_cell', 'fcs'}.issubset(df.columns):
        tmp = df
    else:
        tmp = df.reset_index()

    # Both satellite and cell specified
    if sat_id is not None and cell_id is not None:
        filtered = tmp[(tmp['ra_sat'] == sat_id) & (tmp['ra_cell'] == cell_id)]
        if filtered.empty:
            return None
        # Return just (fc, samples)
        return list(zip(filtered['fcs'], filtered['samples']))

    # Only satellite specified
    if sat_id is not None:
        filtered = tmp[tmp['ra_sat'] == sat_id]
        if filtered.empty:
            return None
        # Return (cell_id, fc, samples)
        return list(zip(filtered['ra_cell'], filtered['fcs'], filtered['samples']))

    # Only cell specified
    if cell_id is not None:
        filtered = tmp[tmp['ra_cell'] == cell_id]
        if filtered.empty:
            return None
        # Return (sat_id, fc, samples)
        return list(zip(filtered['ra_sat'], filtered['fcs'], filtered['samples']))

In [ ]:
# Create the DataFrame using your actual data
sufix = 2
sample = 15  #0 - 9999
fs = 25e6  #sample_frequency
dt = 1/25e6 #period

samples, fcs = load_samples(data_dir,f"{sufix:03d}")
ra_sat, ra_cell = load_data(data_dir, f"{sufix:03d}")

df = pd.DataFrame({
    'ra_sat': ra_sat,
    'ra_cell': ra_cell,
    'fcs':     fcs,
    'samples': list(samples)
})
# Create MultiIndex version
df_indexed = df.set_index(['ra_sat', 'ra_cell'])

# Prepare test parameters based on your actual data
unique_sats  = df['ra_sat'].unique()
unique_cells = df['ra_cell'].unique()
sat0 = unique_sats[0]
cell0 = unique_cells[0]
sat_non = max(unique_sats) + 1
cell_non = max(unique_cells) + 1

# Expected outputs from the original DataFrame
expected_both  = get_signals_v2(df, sat_id=sat0, cell_id=cell0)
expected_sat   = get_signals_v2(df, sat_id=sat0)
expected_cell  = get_signals_v2(df, cell_id=cell0)

# Define test cases
test_cases = [
    ("No filters", {}, None),
    (f"Exact sat={sat0}, cell={cell0}", {'sat_id': sat0, 'cell_id': cell0}, expected_both),
    (f"Only sat_id={sat0}",        {'sat_id': sat0},                               expected_sat),
    (f"Only cell_id={cell0}",      {'cell_id': cell0},                             expected_cell),
    ("Nonexistent sat",            {'sat_id': sat_non},                            None),
    ("Nonexistent cell",           {'cell_id': cell_non},                          None),
]

# Run tests and collect results
results = []
for desc, params, expected in test_cases:
    out_df    = get_signals_v2(df, **params)
    out_index = get_signals_v2(df_indexed, **params)
    results.append({
        "Test": desc,
        "Expected": expected,
        "Original DF": out_df,
        "PASS DF": out_df == expected,
        "MultiIndex": out_index,
        "PASS MI": out_index == expected
    })

# Display results
results_df = pd.DataFrame(results)
print(results_df.to_string(index=False))

                 Test                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   